In [1]:
# Setup and imports
import os
import numpy as np
from pathlib import Path
import json

# Add hloc module to path
import sys
sys.path.append('../modules/hloc')

from hloc import visualization
from hloc.utils import viz_3d
import pycolmap

print('Setup complete')

[2025/09/20 13:17:37 hloc WARNING] hloc requires pycolmap>=3.12.3 but found pycolmap==0.6.1, please upgrade with `pip install --upgrade "pycolmap>=3.12.3"`


Setup complete\!


In [2]:
# Configuration
OUTPUT_DIR = Path("../outputs/hloc_poses")
SFM_DIR = OUTPUT_DIR / "sfm"
POSES_DIR = OUTPUT_DIR / "poses"

print(f"Output directory: {OUTPUT_DIR}")
print(f"SfM directory: {SFM_DIR}")
print(f"Checking file status...")
print(f"  SfM model: {'✓' if SFM_DIR.exists() else '✗'} {SFM_DIR}")
print(f"  Poses: {'✓' if POSES_DIR.exists() else '✗'} {POSES_DIR}")

Output directory: ../outputs/hloc_poses
SfM directory: ../outputs/hloc_poses/sfm
Checking file status...
  SfM model: ✓ ../outputs/hloc_poses/sfm
  Poses: ✓ ../outputs/hloc_poses/poses


In [3]:
# Load exported poses if available
camera_poses_file = POSES_DIR / "camera_poses.json"
trajectory_file = POSES_DIR / "trajectory_tum.txt"

if camera_poses_file.exists():
    print(f"Loading exported camera poses from {camera_poses_file}")
    
    with open(camera_poses_file, 'r') as f:
        camera_poses = json.load(f)
    
    print(f"✓ Loaded {len(camera_poses)} exported camera poses")
    
    # Display sample poses
    print("Sample poses:")
    for i, pose in enumerate(camera_poses[:3]):
        tx, ty, tz = pose['translation']
        print(f"  {pose['image_name']}: position=({tx:.3f}, {ty:.3f}, {tz:.3f})")
        
else:
    print(f"No exported camera poses found at {camera_poses_file}")

if trajectory_file.exists():
    print(f"✓ TUM trajectory file available: {trajectory_file}")
else:
    print(f"No TUM trajectory file found at {trajectory_file}")

Loading exported camera poses from ../outputs/hloc_poses/poses/camera_poses.json
✓ Loaded 128 exported camera poses
Sample poses:
  images/P1180141.JPG: position=(3.753, -0.350, -0.841)
  images/P1180142.JPG: position=(3.736, -0.306, -0.695)
  images/P1180143.JPG: position=(3.701, -0.263, -0.557)
✓ TUM trajectory file available: ../outputs/hloc_poses/poses/trajectory_tum.txt


In [4]:
# Load the reconstruction
try:
    model = pycolmap.Reconstruction(SFM_DIR)
    print(f"✓ Loaded reconstruction from {SFM_DIR}")
    print(f"  Number of registered images: {len(model.images)}")
    print(f"  Number of 3D points: {len(model.points3D)}")
    print(f"  Number of cameras: {len(model.cameras)}")
    
except Exception as e:
    print(f"❌ Failed to load reconstruction: {e}")
    model = None

✓ Loaded reconstruction from ../outputs/hloc_poses/sfm
  Number of registered images: 128
  Number of 3D points: 42910
  Number of cameras: 1


In [ ]:
# 3D Reconstruction Visualization
if model is not None:
    print("Creating 3D reconstruction visualization...")
    
    # Create the 3D figure
    fig = viz_3d.init_figure()
    
    # Plot the reconstruction
    viz_3d.plot_reconstruction(
        fig, model, color="rgba(255,0,0,0.5)", name="reconstruction", points_rgb=True
    )
    
    fig.show()
else:
    print("No reconstruction model available for visualization")

Creating 3D reconstruction visualization...


In [ ]:
# Camera Trajectory Visualization
if model is not None:
    print("Creating camera trajectory visualization...")
    
    # Extract camera positions
    camera_positions = []
    
    for image_id, image in model.images.items():
        # Get camera pose (convert to world coordinates)
        cam_from_world = image.cam_from_world
        world_from_cam = cam_from_world.inverse()
        
        # Extract translation (camera position in world coordinates)
        position = world_from_cam.translation
        camera_positions.append(position)
    
    camera_positions = np.array(camera_positions)
    
    print(f"Extracted {len(camera_positions)} camera positions")
    
    # Create trajectory figure
    fig_traj = viz_3d.init_figure()
    
    # Plot camera positions as points
    viz_3d.plot_points(fig_traj, camera_positions, color="blue", ps=8, name="camera_positions")
    
    # Add trajectory line using plotly
    import plotly.graph_objects as go
    fig_traj.add_trace(go.Scatter3d(
        x=camera_positions[:, 0],
        y=camera_positions[:, 1], 
        z=camera_positions[:, 2],
        mode='lines',
        name='trajectory',
        line=dict(color='red', width=3)
    ))
    
    fig_traj.update_layout(title="Camera Trajectory")
    fig_traj.show()
    
else:
    print("No reconstruction model available for trajectory visualization")

# View HLoC Results

This notebook loads and visualizes the outputs from HLoC camera pose estimation.